# csv des labels numériques des lycee

## Import data  from api

In [105]:
#importing necessary packages
import pandas as pd
import requests
import json

# get data 
#creating the url
url = 'https://data.occitanie.education.gouv.fr/api/records/1.0/search/?dataset=fr-en-occitanie-label-numerique-lycee&q=&rows=10000&facet=annee&facet=rne&facet=departement&facet=label'
#making the request
response = requests.get(url)
#converting the response to json
data = response.json()
#appending the data to the list

#creating an empty list to store the records
records = []

#looping through the records
for record in data['records']:
    #storing the records in the list
    records.append(record['fields'])

#creating a dataframe from the json
df = pd.DataFrame(records)

## Transforming data of df

In [106]:
#transform the label to numeric
df["label"] = pd.to_numeric(df["label"])
df["annee"] = pd.to_numeric(df["annee"])

#sort annee by ascending order
df.sort_values(by="annee",inplace=True)

#create two new columns for longitude and latitude
df['latitude'] = df['position'].apply(lambda x: float(x[0]))
df['longitude'] = df['position'].apply(lambda x: float(x[1]))

# csv des résultats des lycee professionnels

## import data from api

In [107]:
# get data
#creating the url
url = 'https://data.occitanie.education.gouv.fr/api/records/1.0/search/?dataset=fr-en-indicateurs-de-resultat-des-lycees-denseignement-professionnels&q=&rows=10000&facet=etablissement&facet=code_etablissement&facet=annee&facet=ville&facet=academie&facet=departement&facet=secteur_public_1_prive_2&facet=libelle_region_2016'
#making the request
response = requests.get(url)
#converting the response to json
data = response.json()

#creating an empty list to store the records
records = []

#looping through the records
for record in data['records']:
    #storing the records in the list
    records.append(record['fields'])

#creating a dataframe from the json
df2 = pd.DataFrame(records)

## Nettoyage

In [108]:
# nettoyage

# Le lycee "LYCEE PROFESSIONNEL CASTELNOUVEL" a un taux de réussite brut 0
# Il a aussi un effectif_presents_total_secteurs 1, ce qui errone la visualisation (un point très écarté)
# ainsi qu'un taux_mentions_attendu_tous_secteurs Nan
# j'ai donc décidé d'enlever ce lycee
df2.drop(df2[df2['code_etablissement'] == "0312063Z"].index, inplace = True)


## Transform

In [109]:
# transformation

#transform the annee to numeric
df2["annee"] = pd.to_numeric(df2["annee"])
#sort annee by ascending order
df2.sort_values(by="annee",inplace=True)


# transform le taux brut en numerique
df2["taux_brut_de_reussite_total_secteurs"] = pd.to_numeric(df2["taux_brut_de_reussite_total_secteurs"])


# Operations sur les deux csv (merge)
 - csv labels numériques lycee
 - csv résultats scolaires des lycee professionnels

In [110]:
# merge 2 dataframes on the uri (id de l'etablissement scolaire)
df_result = pd.merge(df, df2, left_on='rne', right_on='code_etablissement', how="inner")

In [111]:
# merge 2 dataframes but keep all the lycee that does not have label 
df_result_all = pd.merge(df,df2, left_on='rne', right_on='code_etablissement', how="right")

## Nettoyage df result (resultat des lycées professionels numériques)

In [112]:
#nettoyage (supression) des colonnes ou toutes les valeures sont nulles
df_result.dropna(axis=1,how='all',inplace=True)

#nettoyage (supression) des lignes ou toutes les valeures sont nulles
df_result.dropna(axis=0,how='all',inplace=True)

# L'index 1393 a une valeure ajoutée de réusiite totale = "ND"
# par contre ce lycee a un taux_brut_de_reussite_total_secteurs = 84
# j'ai donc décidé de rempace le "ND" par 0 (neutre) pour ce lycee et pour tous les lycee qui ont
# une valeure ajoutée de réussite totale = "ND" (non définir)
import re
reg_ex1 = r"ND"
reg_ex2 = r"\."
aNegliger = re.compile(f"{reg_ex1}|{reg_ex2}",re.I)
subst = "0"
def apply_reg(str_):
    '''Fonction pour remplacer les "ND" par 0 tout court dans une colonne
        - paramètres : 
            - str_ : la chaine de caractère dans laquelle la fonction va chercher la pattern à nettoyé
        - Return la chaine de caractère nettoyé '''
    if pd.notna(str_):
        return re.sub(aNegliger, subst, str(str_))
    else:
        return str_
    
df_result['va_reu_total'] = df_result['va_reu_total'].apply(apply_reg)

## Nettoyage df result all (resultat de tous les lycées professionels)

In [113]:
#nettoyage (supression) des colonnes ou toutes les valeures sont nulles
df_result_all.dropna(axis=1,how='all',inplace=True)

#nettoyage (supression) des lignes ou toutes les valeures sont nulles
df_result_all.dropna(axis=0,how='all',inplace=True)

# L'index 1393 a une valeure ajoutée de réusiite totale = "ND"
# par contre ce lycee a un taux_brut_de_reussite_total_secteurs = 84
# j'ai donc décidé de rempace le "ND" par 0 (neutre) pour ce lycee et pour tous les lycee qui ont
# une valeure ajoutée de réussite totale = "ND" (non définir)
df_result_all['va_reu_total'] = df_result_all['va_reu_total'].apply(apply_reg)

## Transform df qui contient les resultat des lycées labelisés seulement (df_result)

In [114]:
# transformer les dates en numériques pour la prochaine opération
df_result["annee_x"] = pd.to_numeric(df_result["annee_x"])
df_result["annee_y"] = pd.to_numeric(df_result["annee_y"])

# ajouter une colonne qui contient boolean (resultat après obtention label ou pas)
# True si oui, false sinon
# les resultats des lycee après l'obtention de leurs labels 
# (annee_x pour obtention label, annee_y pour passage examens de baccalauréat)
df_result["resultat_apres_label"] = (df_result["annee_y"] >= df_result["annee_x"])

# transformer la valeur ajoutée de réussites totale en numérique
df_result["va_reu_total"] = pd.to_numeric(df_result["va_reu_total"])

# transorm taux_reussite_attendu_france_total_secteurs to numeric
df_result["taux_reussite_attendu_france_total_secteurs"] = pd.to_numeric(df_result["taux_reussite_attendu_france_total_secteurs"])


## Transform df qui contient les résultats de tous les lycées inclus sont qui sont labelisés (df_result_all)

In [115]:
# transformer les dates en numériques pour la prochaine opération
# transformer les dates en numériques pour la prochaine opération
df_result_all["annee_y"] = pd.to_numeric(df_result_all["annee_y"])

# Creer une colonne pour dire si le lycee est labelisé : True/False
df_result_all["label_true"] = (pd.notna(df_result_all["rne"]))

# ajouter une colonne qui contient boolean (resultat après obtention label ou pas)
# True si oui, false sinon
# les resultats des lycee après l'obtention de leurs labels 
# (annee_x pour obtention label, annee_y pour passage examens de baccalauréat)
df_result_all["resultat_apres_label"] = (df_result_all["annee_y"] >= df_result_all["annee_x"]) & (df_result_all["label_true"] == True)

# remplacer tous les labels à 0 where examen passé avant 2017
df_result_all.loc[df_result_all["resultat_apres_label"] == False, "label"] = 0

# transformer la valeur ajoutée de réussites totale en numérique
df_result_all["va_reu_total"] = pd.to_numeric(df_result_all["va_reu_total"])

# transorm taux_reussite_attendu_france_total_secteurs to numeric
df_result_all["taux_reussite_attendu_france_total_secteurs"] = pd.to_numeric(df_result_all["taux_reussite_attendu_france_total_secteurs"])

## Infos

In [116]:
df_result.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3757 entries, 0 to 3756
Columns: 136 entries, label to resultat_apres_label
dtypes: bool(1), float64(18), int64(6), object(111)
memory usage: 3.9+ MB


# Transform for visualisations

In [117]:
# re transform annee to str so it can be a discrete value for visualisations (discrete value)
df_result["annee_x"] = df_result["annee_x"].apply(str)
df_result["annee_y"] = df_result["annee_y"].apply(str)

df_result_all["annee_x"] = df_result_all["annee_x"].apply(str)
df_result_all["annee_y"] = df_result_all["annee_y"].apply(str)

# Visualisation 

In [118]:
# Import necessary libraries
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import folium # for maps
import plotly.graph_objects as go

## Analyse général

In [119]:
# La répartition des Ecole, lycce et collège en france

nbre_lycee_professionnel = df_result_all['code_etablissement'].nunique()
nbre_lycee_professionel_labelise = df_result_all['rne'].nunique()
nbre_lycee_professionnel_non_labelise = nbre_lycee_professionnel - nbre_lycee_professionel_labelise
values = [nbre_lycee_professionnel_non_labelise,nbre_lycee_professionel_labelise]
labels = ["nombre de lycées professionels non labelisés pour lesquelles on connait le resultat", "nombre de lycées professionels labelisés pour lesquelles on connait le resultat"]

fig = go.Figure(data=[go.Pie(labels=labels, values=values, title = "La proportions des Lycées labelisés parmis les professionels")])
fig.show()

In [120]:
# La variation du nombre des lycées labelisés selon les années
df_proportion_lycee_labelise_annee = df_result.groupby("annee_x")["rne"].nunique()
df_proportion_lycee_labelise_annee = df_proportion_lycee_labelise_annee.reset_index()

#plotting a histogram 
fig = px.histogram(df_proportion_lycee_labelise_annee, x="annee_x", y="rne",
                   color="annee_x",
                      labels={"code_etablissement" : "nombre de lycee labelisés"})
fig.update_layout(title_text="La variation du nombre des lycées labelisés selon les années")
fig.show()

**le nombre de lycées professionels labelisés a augmente de 103,17 % entre 2017 et 2021**

In [121]:
# La variation du nombre des lycées non labelisés selon les années
df_proportion_lycee_non_labelise_annee = df_result_all.query("label_true == False").groupby("annee_y")["code_etablissement"].nunique()
df_proportion_lycee_non_labelise_annee = df_proportion_lycee_non_labelise_annee.reset_index()

#plotting a histogram 
fig = px.histogram(df_proportion_lycee_non_labelise_annee, x="annee_y", y="code_etablissement",
                   color="annee_y",
                      labels={"code_etablissement" : "nombre de lycee non labelisés"})
fig.update_layout(title_text="La variation du nombre des lycées non labelisés selon les années")
fig.show()

**Le nombre de lycées professionels non labelisés a diminué de 8.7% entre 2012 et 2021**

In [122]:
# La variation du nombre des lycées professionels (labelisé ou non) selon les années
df2["annee"] = df2["annee"].apply(str)
df_proportion_lycee_tout_annee = df2.groupby("annee")["code_etablissement"].nunique()
df_proportion_lycee_tout_annee = df_proportion_lycee_tout_annee.reset_index()
df_proportion_lycee_tout_annee

#plotting a histogram 
fig = px.histogram(df_proportion_lycee_tout_annee, x="annee", y="code_etablissement",
                   color="annee",
                      labels={"code_etablissement" : "nombre de lycee non labelisés"})
fig.update_layout(title_text="La variation du nombre des lycées professionels (labelisés et non labelisés) selon les années")
fig.show()

**Le nombre des lycées professionels (labelisés et non labelisé) a augmenté de 11.3% entre 2012 et 2021**

### Conclusion

**Au fil des années, les lycées non labelisés diminuent et obtiennent des labels et deviennent alors labelisés.
De ce fait le nombre des lycées labelisés augmentent.**
**Cependant, l'augmentation du nombre des lycées professionels labelisés (103%) entre 2017 et 2021, n'est pas seulement expliqué par la diminution du nombre des lycées non labelisés (8,7%) entre 2012 et 2021.
Cette augmentation est aussi du au fait que des nouveaux lycées labelisés sont introduits chaque année**

## Analyse du taux brut de réussite des élèves dans les lycées

**Taux de réussite constaté**

- Le taux de réussite au baccalauréat est la proportion, parmi les élèves présents à l’examen, de ceux qui ont obtenu le diplôme
- Le graphique ci-dessous montre que le moyenne du taux de réussite est presque similaire selon que l'école
    a un abel 1 ou 3.
- Il est donc intéréssant d'aller voir qu'elle étaient les moyennes de taux de réussite de ces écoles avant
    obtention de leurs labels numérique !

In [143]:
# transform label to numeric
df_result["label"] = pd.to_numeric(df_result["label"])
#sort label by ascending order
df_result.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result["label"] = df_result["label"].apply(str)

#plotting a histogram
fig = px.histogram(df_result[df_result["resultat_apres_label"] == True], x="label", y="taux_brut_de_reussite_total_secteurs", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des taux bruts de réussites des lycee après obtention de leurs labels (tous secteurs) selon les labels")
fig.show()

In [145]:
# transform label to numeric
df_result_all["label"] = pd.to_numeric(df_result_all["label"])
#sort label by ascending order
df_result_all.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["label"] = df_result_all["label"].apply(str)

#plotting a histogram
fig = px.histogram(df_result_all, x="label", y="taux_brut_de_reussite_total_secteurs", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des taux bruts de réussites des lycee après obtention de leurs labels (tous secteurs) selon les labels")
fig.show()

**Comparaison de la moyenne du taux de réussite constaté avant et après obtention des labels numériques**

- Le graphique ci-dessous montre une amélioration des taux de réussite des écoles après obtention de leurs labels
    numérique !
- IL est donc intéréssant d'aller chercher pourquoi ? est ce que l'école a apporté plus de valeur pour les 
    élèves grace au numérique ?

In [125]:
#plotting a histogram 
fig = px.histogram(df_result, x="departement_y", y="taux_brut_de_reussite_total_secteurs", nbins=10,
                       histfunc="avg", color="departement_y",
                       facet_row="resultat_apres_label",
                      labels={"taux_brut_de_reussite_total_secteurs" : "taux brut de réussite"})
fig.update_layout(title_text="La moyenne des taux bruts de réussites (tous secteurs) selon les départements - avant et après obtention labels")
fig.show()

### La moyenne des taux bruts de réussites (tous secteurs) avant et après obtention labels

In [126]:
#plotting a histogram 
fig = px.histogram(df_result, x="resultat_apres_label", y="taux_brut_de_reussite_total_secteurs", nbins=10,
                       histfunc="avg", color="resultat_apres_label",
                      labels={"taux_brut_de_reussite_total_secteurs" : "taux brut de réussite"})
fig.update_layout(title_text="La moyenne des taux bruts de réussites (tous secteurs) avant et après obtention labels")
fig.show()

In [127]:
#plotting a histogram 
fig = px.histogram(df_result, x="rne", y="taux_brut_de_reussite_total_secteurs", nbins=10, histfunc="avg", color="departement_y", facet_row="resultat_apres_label",
                  labels={"taux_brut_de_reussite_total_secteurs" : "taux brut de réussite"})
fig.update_layout(title_text="La moyenne des taux bruts de réussites de chaque lycée (tous secteurs) avant et après obtention labels")
fig.show()

**Pourquoi certains lycées n'apparaissent pas dans le resultat après labels malgré qu'ils ont des labels ?**
- simplement parce ces lycées n'ont pas eu de passages d'examens après obtentions de labels (peut etre étrange mais 
    voici les données suivantes comme exemple pour l'école 0480009Z

In [128]:
df_result[df_result['rne'] == "0480009Z"][["label","annee_x","annee_y","code_etablissement","resultat_apres_label"]]

label annee_x annee_y code_etablissement  resultat_apres_label
836     1    2017    2016           0480009Z                 False
837     1    2018    2016           0480009Z                 False
838     1    2019    2016           0480009Z                 False
839     1    2021    2016           0480009Z                 False

### On va voir la différence des résultats entre les lycées labelisés et ceux qui ne le sont pas

In [139]:
#plotting a histogram 
fig = px.histogram(df_result_all, x="resultat_apres_label", y="taux_brut_de_reussite_total_secteurs", nbins=10,
                       histfunc="avg", color="resultat_apres_label",
                      labels={"taux_brut_de_reussite_total_secteurs" : "taux brut de réussite"})
fig.update_layout(title_text="La moyenne des taux bruts de réussites sans et avec labels")
fig.show()

In [142]:
#plotting a bocplot 
fig = px.box(df_result_all, x="resultat_apres_label", y="taux_brut_de_reussite_total_secteurs",
             color="resultat_apres_label",
            labels={"taux_brut_de_reussite_total_secteurs" : "taux brut de réussite"})
fig.update_layout(title_text="La variance des taux bruts de réussites sans et avec labels")
fig.show()

In [26]:
#plotting a bocplot 
fig = px.box(df_result_all, x="annee_y", y="taux_brut_de_reussite_total_secteurs",
             color="label_true",
            labels={"taux_brut_de_reussite_total_secteurs" : "taux brut de réussite"})
fig.update_layout(title_text="La moyenne des taux bruts de réussites sans et avec labels par année")
fig.show()

**On constate que les lycées professionels non labelisés ont un meilleur résultat que ceux labelisés (toutes années confondues)**
 - On se demande pourquoi ?
 - On sait que parmis les lycées professionels, 33% ne sont pas labelisés, et 67% sont labelisés.
 - Alors nous souhaitons répondre à la question suivante : y'a t'il un effet de la labélisation sur le taux de réussite des lycées professionels ?
 - Pour cela on pose les hypothèses suivantes : 
     - H0 : La labélisation d'un lycee professionel n'a pas d'effet sur son taux brut de réussite tous secteurs
     - H1 : La labélisation d'un lycee professionel a un effet sur son taux brut de réussite tous secteurs

### Covid
**Nous constatons un pic de taux de réussite des lycées professionels en 2020, puis une diminution de ce taux en 2021**

## Analyse de la valeur ajoutée de réussite 
- la valeur ajoutée de l’établissement est la différence entre le taux constaté de l’établissement et le taux attendu. 

    **Valeur ajoutée = taux constaté – taux attendu**
    

- Le graphique ci-dessous montre une moyenne de valeur ajoutée de label 3 plus petite que label 1.
    C'est étonnant, mais est-ce que ça veut dire que les écoles ayant un label 3 ont contribué moins
    à la réussite des élèves ? Pas nécessairement.
- En effet, peut etre que les écoles ayant un label 3, ont un taux de réussite attendu beaucoup plus elevé 
    que les écoles avec un label plus faible. De ce fait, l'augmentation du taux de réussite attendu 
    peut diminuer la valeur ajoutée de l'école.

In [27]:
# transform label to numeric
df_result["label"] = pd.to_numeric(df_result["label"])
#sort label by ascending order
df_result.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result["label"] = df_result["label"].apply(str)

#plotting a histogram 
fig = px.histogram(df_result[df_result["resultat_apres_label"] == True], x="label", y="va_reu_total", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des valeurs ajoutées de réussites (tous secteurs) selon les labels")
fig.show()

**Comparaison des valeurs ajoutées des écoles avant et après obtention des labels numériques**

- le graphique ci-dessous montre une véritables amélioration des valeurs ajoutée des écoles après obtention de labels. Surtout pour le département de LOZERE pour lequel la valeur ajoutée est passée du **-** à **+** !

In [28]:
#plotting a histogram 
fig = px.histogram(df_result, x="departement_y", y="va_reu_total", nbins=10, histfunc="avg", color="departement_y", facet_row="resultat_apres_label")
fig.update_layout(title_text="La moyenne des valeurs ajoutés de réussites (tous secteurs) selon les départements avant et après obtention labels")
fig.show()

In [29]:
#plotting a histogram 
fig = px.histogram(df_result, x="resultat_apres_label", y="va_reu_total", nbins=10, histfunc="avg", color="resultat_apres_label")
fig.update_layout(title_text="La moyenne des valeurs ajoutés de réussites (tous secteurs) avant et après obtention labels")
fig.show()

### Comparaison de la moyenne des valeurs ajoutés de réussites (tous secteurs) des lycées professinels sans et avec labels

In [30]:
#plotting a histogram 
fig = px.histogram(df_result_all, x="label_true", y="va_reu_total", nbins=10, histfunc="avg", color="label_true")
fig.update_layout(title_text="La moyenne des valeurs ajoutés de réussites (tous secteurs) sans et avec labels")
fig.show()

In [31]:
#plotting a bocplot 
fig = px.box(df_result_all, x="label_true", y="va_reu_total",
             color="label_true",
            labels={"va_reu_total" : "taux de valeur ajoutée total secteurs"})
fig.update_layout(title_text="La variance des taux bruts de réussites sans et avec labels")
fig.show()

In [32]:
#plotting a bocplot 
fig = px.box(df_result_all, x="annee_y", y="va_reu_total",
             color="label_true",
            labels={"va_reu_total" : "taux de valeur ajoutée total secteurs"})
fig.update_layout(title_text="La variance des taux bruts de réussites sans et avec labels par année")
fig.show()

## Analyse du taux de réussite attendu en france (total secteurs)

In [33]:
# transform label to numeric
df_result["label"] = pd.to_numeric(df_result["label"])
#sort label by ascending order
df_result.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result["label"] = df_result["label"].apply(str)

#plotting a histogram 
fig = px.histogram(df_result[df_result["resultat_apres_label"] == True], x="label", y="taux_reussite_attendu_france_total_secteurs", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france (tous secteurs) selon les labels")
fig.show()

### Comparaison du taux de réussite des élèces aux lycées professionels attendu en france total secteurs avant et  après obtention des labels

In [34]:
#plotting a histogram 
fig = px.histogram(df_result, x="departement_y", y="taux_reussite_attendu_france_total_secteurs", nbins=10,
                       histfunc="avg", color="departement_y",
                       facet_row="resultat_apres_label",
                      labels={"taux_reussite_attendu_france_total_secteurs" : "Taux_réussite_attendu"})
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france (tous secteurs) selon les départements - avant et après obtention labels")
fig.show()

In [35]:
#plotting a histogram 
fig = px.histogram(df_result, x="resultat_apres_label", y="taux_reussite_attendu_france_total_secteurs", nbins=10,
                       histfunc="avg", color="resultat_apres_label",
                      labels={"taux_reussite_attendu_france_total_secteurs" : "Taux_réussite_attendu"})
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france (tous secteurs) avant et après obtention labels")
fig.show()

### Comparaison du taux de réussite des élèces aux lycées professionels attendu en france total secteurs sans et avec labels

In [36]:
#plotting a histogram 
fig = px.histogram(df_result_all, x="label_true", y="taux_reussite_attendu_france_total_secteurs", nbins=10,
                       histfunc="avg", color="label_true",
                      labels={"taux_reussite_attendu_france_total_secteurs" : "Taux_réussite_attendu"})
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france (tous secteurs) sans et avec labels")
fig.show()

## Analyse temporelles

In [37]:
fig = px.line(df_result_all,
                 x = "annee_y",
                 y = "taux_brut_de_reussite_total_secteurs",
                 color = "code_etablissement",
                 hover_name="taux_brut_de_reussite_total_secteurs",
             hover_data=["label"],
             title = "Le taux de réussite des lycées professionels non labeisés en 2012 en fonction des années")

plt.tight_layout()
fig.show()

<Figure size 432x288 with 0 Axes>

In [38]:
from bioinfokit.analys import stat

In [39]:
res = stat()
res.anova_stat(df=df_result_all, res_var='taux_brut_de_reussite_total_secteurs', anova_model='taux_brut_de_reussite_total_secteurs ~ C(label_true)')
res.anova_summary
# output (ANOVA F and p value)

df         sum_sq      mean_sq          F        PR(>F)
C(label_true)     1.0    3954.774882  3954.774882  47.713192  5.659683e-12
Residual       4286.0  355251.122273    82.886403        NaN           NaN

In [40]:
res2 = stat()
res2.anova_stat(df=df_result_all, res_var='va_reu_total', anova_model='va_reu_total ~ C(label_true)')
res2.anova_summary
# output (ANOVA F and p value)

df         sum_sq    mean_sq        F   PR(>F)
C(label_true)     1.0       9.839342   9.839342  0.21278  0.64462
Residual       4286.0  198192.249277  46.241775      NaN      NaN

In [41]:
condition = (df_result_all["label_true"] == False) & (df_result_all["annee_x"] > "2017")
df_result_all[condition]

label annee_x             localite departement_x  \
0       1.0  2018.0  Beaumont-de-Lomagne           082   
1       1.0  2019.0  Beaumont-de-Lomagne           082   
2       1.0  2021.0  Beaumont-de-Lomagne           082   
3       NaN     nan                  NaN           NaN   
4       NaN     nan                  NaN           NaN   
...     ...     ...                  ...           ...   
4243    NaN     nan                  NaN           NaN   
4269    NaN     nan                  NaN           NaN   
4270    NaN     nan                  NaN           NaN   
4277    NaN     nan                  NaN           NaN   
4278    NaN     nan                  NaN           NaN   

                                      nom_etablissement  \
0     Lycée professionnel des Métiers du Bâtiment et...   
1     Lycée professionnel des Métiers du Bâtiment et...   
2     Lycée professionnel des Métiers du Bâtiment et...   
3                                                   NaN   
4                                                   NaN   
...                                                 ...   
4243                                                NaN   
4269                                                NaN   
4270                                                NaN   
4277                                                NaN   
4278                                                NaN   

                             position       rne   latitude  longitude  \
0     [43.8769993582, 0.977210268058]  0820001F  43.876999    0.97721   
1     [43.8769993582, 0.977210268058]  0820001F  43.876999    0.97721   
2     [43.8769993582, 0.977210268058]  0820001F  43.876999    0.97721   
3                                 NaN       NaN        NaN        NaN   
4                                 NaN       NaN        NaN        NaN   
...                               ...       ...        ...        ...   
4243                              NaN       NaN        NaN        NaN   
4269                              NaN       NaN        NaN        NaN   
4270                              NaN       NaN        NaN        NaN   
4277                              NaN       NaN        NaN        NaN   
4278                              NaN       NaN        NaN        NaN   

     taux_acces_attendu_france_seconde_bac  ...  \
0                                       61  ...   
1                                       61  ...   
2                                       61  ...   
3                                       59  ...   
4                                       52  ...   
...                                    ...  ...   
4243                                   NaN  ...   
4269                                   NaN  ...   
4270                                   NaN  ...   
4277                                   NaN  ...   
4278                                   NaN  ...   

     taux_reussite_attendu_acad_services  va_reu_communication  \
0                                    NaN                   NaN   
1                                    NaN                   NaN   
2                                    NaN                   NaN   
3                                     91                   NaN   
4                                    NaN                   NaN   
...                                  ...                   ...   
4243                                 NaN                   NaN   
4269                                 NaN                   NaN   
4270                                 NaN                     0   
4277                                 NaN                   NaN   
4278                                 NaN                   NaN   

     va_men_communication taux_brut_de_reussite_communication_et_information  \
0                     NaN                                                NaN   
1                     NaN                                                NaN   
2                     NaN                                                NaN 